# Preprocesado

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sb
from ydata_profiling import ProfileReport
import sklearn
import datetime

from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder,OrdinalEncoder,MinMaxScaler
from sklearn.pipeline import Pipeline
from sklearn import set_config
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score, roc_curve, auc

from sklearn.metrics import accuracy_score, confusion_matrix, recall_score, precision_score, f1_score, classification_report

In [2]:
cars_data = pd.read_excel("2021_Second Car Sale.xlsx",sheet_name = "M02")

In [3]:
#se convierten datos de tipo datetime a string que previamente se habian identificado, esto con el fin de evitar problemas en el analisis de datos
cars_data.Model = cars_data.Model.replace({datetime.datetime(2021, 9, 3, 0, 0) : "3-sep", datetime.datetime(2021, 9, 5, 0, 0) : "5-sep"})

In [4]:
#se crea un array con los valores unicos de la columna "Model"
array_names = cars_data["Model"].unique()
array_names

array(['1 Series M', '1 Series', 100, '124 Spider', '190-Class',
       '2 Series', 200, '200SX', '240SX', 240, 2, '3 Series Gran Turismo',
       '3 Series', '300-Class', '3000GT', 300, '300M', '300ZX', 323,
       '350-Class', '350Z', 360, '370Z', 3, '4 Series Gran Coupe',
       '4 Series', '400-Class', '420-Class', '456M', '458 Italia', '4C',
       '4Runner', '5 Series Gran Turismo', '5 Series', '500-Class',
       '500e', 500, '500L', '500X', 550, '560-Class', '570S', '575M', 57,
       599, 5, '6 Series Gran Coupe', '6 Series', '600-Class', 6000,
       '612 Scaglietti', 626, 62, '650S Coupe', '650S Spider', 6,
       '7 Series', '718 Cayman', 740, 760, 780, '8 Series', 80, 850, 86,
       '9-2X', '9-3 Griffin', '3-sep', '9-4X', '5-sep', '9-7X', 9000, 900,
       90, 911, 928, 929, 940, 944, 960, 968, 'A3', 'A4 allroad', 'A4',
       'A5', 'A6', 'A7', 'A8', 'Acadia Limited', 'Acadia', 'Accent',
       'Acclaim', 'Accord Crosstour', 'Accord Hybrid',
       'Accord Plug-In Hybrid'

In [5]:
#se trasforman los valores de "Model" de string a int con valores que empiezan en "1" para realizar un analisis de los datos
for i, j in enumerate(array_names):
    cars_data.Model = cars_data.Model.replace({j:i})

C:\Users\User\AppData\Local\Temp\ipykernel_8924\1285059754.py:3: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  cars_data.Model = cars_data.Model.replace({j:i})


In [6]:
cars_data

Make  Model  Year                Engine Fuel Type  Engine HP  \
0          BMW      0  2011     premium unleaded (required)      335.0   
1          BMW      1  2011     premium unleaded (required)      300.0   
2          BMW      1  2011     premium unleaded (required)      300.0   
3          BMW      1  2011     premium unleaded (required)      230.0   
4          BMW      1  2011     premium unleaded (required)      230.0   
...        ...    ...   ...                             ...        ...   
11909    Acura    913  2012     premium unleaded (required)      300.0   
11910    Acura    913  2012     premium unleaded (required)      300.0   
11911    Acura    913  2012     premium unleaded (required)      300.0   
11912    Acura    913  2013  premium unleaded (recommended)      300.0   
11913  Lincoln    914  2006                regular unleaded      221.0   

       Engine Cylinders Transmission Type      Driven_Wheels  Number of Doors  \
0                   6.0            MANUAL   rear wheel drive              2.0   
1                   6.0            MANUAL   rear wheel drive              2.0   
2                   6.0            MANUAL   rear wheel drive              2.0   
3                   6.0            MANUAL   rear wheel drive              2.0   
4                   6.0            MANUAL   rear wheel drive              2.0   
...                 ...               ...                ...              ...   
11909               6.0         AUTOMATIC    all wheel drive              4.0   
11910               6.0         AUTOMATIC    all wheel drive              4.0   
11911               6.0         AUTOMATIC    all wheel drive              4.0   
11912               6.0         AUTOMATIC    all wheel drive              4.0   
11913               6.0         AUTOMATIC  front wheel drive              4.0   

                             Market Category Vehicle Size  Vehicle Style  \
0      Factory Tuner,Luxury,High-Performance      Compact          Coupe   
1                         Luxury,Performance      Compact    Convertible   
2                    Luxury,High-Performance      Compact          Coupe   
3                         Luxury,Performance      Compact          Coupe   
4                                     Luxury      Compact    Convertible   
...                                      ...          ...            ...   
11909             Crossover,Hatchback,Luxury      Midsize  4dr Hatchback   
11910             Crossover,Hatchback,Luxury      Midsize  4dr Hatchback   
11911             Crossover,Hatchback,Luxury      Midsize  4dr Hatchback   
11912             Crossover,Hatchback,Luxury      Midsize  4dr Hatchback   
11913                                 Luxury      Midsize          Sedan   

       highway MPG  city mpg  Popularity   MSRP  
0               26        19        3916  46135  
1               28        19        3916  40650  
2               28        20        3916  36350  
3               28        18        3916  29450  
4               28        18        3916  34500  
...            ...       ...         ...    ...  
11909           23        16         204  46120  
11910           23        16         204  56670  
11911           23        16         204  50620  
11912           23        16         204  50920  
11913           26        17          61  28995  

[11914 rows x 16 columns]

In [7]:
#reporte del analisis de los datos
perfil = ProfileReport(cars_data, title = 'Reporte')
perfil

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [8]:
#se devuelve a los valores originales de "Model"
for i, j in enumerate(array_names):
    cars_data.Model = cars_data.Model.replace({i:j})

In [9]:
#se eliminan los valores nulos
data = cars_data.dropna()
data

Make       Model  Year                Engine Fuel Type  Engine HP  \
0          BMW  1 Series M  2011     premium unleaded (required)      335.0   
1          BMW    1 Series  2011     premium unleaded (required)      300.0   
2          BMW    1 Series  2011     premium unleaded (required)      300.0   
3          BMW    1 Series  2011     premium unleaded (required)      230.0   
4          BMW    1 Series  2011     premium unleaded (required)      230.0   
...        ...         ...   ...                             ...        ...   
11909    Acura         ZDX  2012     premium unleaded (required)      300.0   
11910    Acura         ZDX  2012     premium unleaded (required)      300.0   
11911    Acura         ZDX  2012     premium unleaded (required)      300.0   
11912    Acura         ZDX  2013  premium unleaded (recommended)      300.0   
11913  Lincoln      Zephyr  2006                regular unleaded      221.0   

       Engine Cylinders Transmission Type      Driven_Wheels  Number of Doors  \
0                   6.0            MANUAL   rear wheel drive              2.0   
1                   6.0            MANUAL   rear wheel drive              2.0   
2                   6.0            MANUAL   rear wheel drive              2.0   
3                   6.0            MANUAL   rear wheel drive              2.0   
4                   6.0            MANUAL   rear wheel drive              2.0   
...                 ...               ...                ...              ...   
11909               6.0         AUTOMATIC    all wheel drive              4.0   
11910               6.0         AUTOMATIC    all wheel drive              4.0   
11911               6.0         AUTOMATIC    all wheel drive              4.0   
11912               6.0         AUTOMATIC    all wheel drive              4.0   
11913               6.0         AUTOMATIC  front wheel drive              4.0   

                             Market Category Vehicle Size  Vehicle Style  \
0      Factory Tuner,Luxury,High-Performance      Compact          Coupe   
1                         Luxury,Performance      Compact    Convertible   
2                    Luxury,High-Performance      Compact          Coupe   
3                         Luxury,Performance      Compact          Coupe   
4                                     Luxury      Compact    Convertible   
...                                      ...          ...            ...   
11909             Crossover,Hatchback,Luxury      Midsize  4dr Hatchback   
11910             Crossover,Hatchback,Luxury      Midsize  4dr Hatchback   
11911             Crossover,Hatchback,Luxury      Midsize  4dr Hatchback   
11912             Crossover,Hatchback,Luxury      Midsize  4dr Hatchback   
11913                                 Luxury      Midsize          Sedan   

       highway MPG  city mpg  Popularity   MSRP  
0               26        19        3916  46135  
1               28        19        3916  40650  
2               28        20        3916  36350  
3               28        18        3916  29450  
4               28        18        3916  34500  
...            ...       ...         ...    ...  
11909           23        16         204  46120  
11910           23        16         204  56670  
11911           23        16         204  50620  
11912           23        16         204  50920  
11913           26        17          61  28995  

[8084 rows x 16 columns]

In [10]:
array_features = ["Make", "Year", "Engine Fuel Type", "Engine HP", "Engine Cylinders", "Transmission Type", "Driven_Wheels", "Number of Doors", "Market Category", "Vehicle Size", "Vehicle Style", "highway MPG", "city mpg", "Popularity", "MSRP"]

for i, j in enumerate(array_features):
    relacion = pd.crosstab(index=data[j],
                columns=data['Model'], margins=True)
    print(relacion)
    print('\n')

Model           2   3   5   6  928  940  944  960  968  9000  ...  Zephyr  \
Make                                                          ...           
Acura           0   0   0   0    0    0    0    0    0     0  ...       0   
Alfa Romeo      0   0   0   0    0    0    0    0    0     0  ...       0   
Aston Martin    0   0   0   0    0    0    0    0    0     0  ...       0   
Audi           15   0   0   6    0    0    0    0    6     0  ...       0   
BMW             0   0  17   0    0    0    0    0    0     0  ...       0   
Bentley         0   0   0   0    0    0    0    0    0     0  ...       0   
Bugatti         0   0   0   0    0    0    0    0    0     0  ...       0   
Buick           0   0   0   0    0    0    0    0    0     0  ...       0   
Cadillac        0   0   0   0    0    0    0    0    0     0  ...       0   
Chevrolet       0   0   0   0    0    0    0    0    0     0  ...       0   
Chrysler        0   0   0  23    0    0    0    0    0     0  ...       0   

Model                                          2   3   5   6  928  940  944  \
Engine Fuel Type                                                              
diesel                                         0   0   0   0    0    0    0   
electric                                       0   0   0   0    0    0    0   
flex-fuel (premium unleaded recommended/E85)   0   0   0   0    0    0    0   
flex-fuel (premium unleaded required/E85)      0   0   0   0    0    0    0   
flex-fuel (unleaded/E85)                       0   0   0  23    0    0    0   
premium unleaded (recommended)                 0   3   8   0    0    0    0   
premium unleaded (required)                    0   0   9   0    0    0    0   
regular unleaded                              27  35   0   6    3   14    4   
All                                           27  38  17  29    3   14    4   

Model                                         960  968  9000  ...  Zephyr  \
Engine Fuel Type                                     

Model               2   3   5   6  928  940  944  960  968  9000  ...  Zephyr  \
Driven_Wheels                                                     ...           
all wheel drive     6   0   7  11    0    0    0    0    3     0  ...       0   
four wheel drive    0   0   0   0    0    0    0    0    0     0  ...       0   
front wheel drive  21  35   0  18    0    0    0    0    3    10  ...       1   
rear wheel drive    0   3  10   0    3   14    4    6   13     0  ...       0   
All                27  38  17  29    3   14    4    6   19    10  ...       1   

Model              allroad  allroad quattro  i3  iM  iQ  tC  xA  xD   All  
Driven_Wheels                                                              
all wheel drive          8                8   0   0   0   0   0   0  2158  
four wheel drive         0                0   0   0   0   0   0   0   646  
front wheel drive        0                0   0   2   4  14   6  10  2879  
rear wheel drive         0                0   4   0 

Model         2   3   5   6  928  940  944  960  968  9000  ...  Zephyr  \
highway MPG                                                 ...           
12            0   0   0   0    0    0    0    0    0     0  ...       0   
13            0   0   0   0    0    0    0    0    0     0  ...       0   
14            0   0   0   0    0    0    0    0    0     0  ...       0   
15            0   0   0   0    0    0    0    0    0     0  ...       0   
16            0   0   0   0    0    0    0    0    7     0  ...       0   
17            0   0   0   0    3    0    0    0    0     0  ...       0   
18            0   0   0   0    0    0    0    0    0     0  ...       0   
19            0   0   0   0    0    0    0    0    0     0  ...       0   
20            2   0   0   2    0    0    0    0    0     0  ...       0   
21            4   0   0   0    0    0    0    0    0     0  ...       0   
22            3   0   0   3    0    6    0    0    3     0  ...       0   
23            0   0   0  

Model        2   3   5   6  928  940  944  960  968  9000  ...  Zephyr  \
Popularity                                                 ...           
2            0   0   0   0    0    0    0    0    0     0  ...       0   
21           0   0   0   0    0    0    0    0    0     0  ...       0   
26           0   0   0   0    0    0    0    0    0     0  ...       0   
61           0   0   0   0    0    0    0    0    0     0  ...       1   
67           0   0   0   0    0    0    0    0    7     0  ...       0   
86           0   0   0   0    0    0    0    0    0     0  ...       0   
105          0   0   0   0    0    0    0    0    0     0  ...       0   
113          0   0   0   0    0    0    0    0    0     0  ...       0   
130          0   0   0   0    0    0    0    0    0     0  ...       0   
155          0   0   0   0    0    0    0    0    0     0  ...       0   
190          0   0   0   0    0    0    0    0    0     0  ...       0   
204          0   0   0   0    0    0  

In [11]:
data.columns

Index(['Make', 'Model', 'Year', 'Engine Fuel Type', 'Engine HP',
       'Engine Cylinders', 'Transmission Type', 'Driven_Wheels',
       'Number of Doors', 'Market Category', 'Vehicle Size', 'Vehicle Style',
       'highway MPG', 'city mpg', 'Popularity', 'MSRP'],
      dtype='object')

In [12]:
data.to_csv('data.csv', index=False)

In [13]:
from IPython.display import FileLink
FileLink('data.csv')

C:\Users\User\Jupyter\Untitled Folder\data.csv